In [1]:
import os
import numpy as np

import pandas as pd
from sklearn.model_selection import train_test_split

import tensorflow as tf
from tensorflow.contrib.learn.python.learn.metric_spec import MetricSpec

Using TensorFlow backend.


In [5]:
path = "./data/"
data = pd.read_csv("./data/2018_4_21_22_38.csv",na_values=['NA','?'])

In [6]:
data.head()

Time  Speed  Shift  Load  Acc _Total  RPM     Pitch  Acc _Lat  Passengers  \
0  0.023    0.0      0   0.0         0.0  0.0  0.035780       0.0           0   
1  0.027    0.0      0   0.0         0.0  0.0  0.036828       0.0           0   
2  0.037    0.0      0   0.0         0.0  0.0  0.037882       0.0           0   
3  0.047    0.0      0   0.0         0.0  0.0  0.038939       0.0           0   
4  0.057    0.0      0   0.0         0.0  0.0  0.040000       0.0           0   

   Car_Load  AC_Con  Window_Open  Radio_volume  Rain_intensity  Visibility  \
0         3       0            5             0               0          10   
1         3       0            5             0               0          10   
2         3       0            5             0               0          10   
3         3       0            5             0               0          10   
4         3       0            5             0               0          10   

   welbeing  Rush  class  
0         2     0      1  
1         2     0      1  
2         2     0      1  
3         2     0      1  
4         2     0      1

In [7]:
data.describe().transpose()

count         mean         std       min         25%  \
Time            24140.0   120.713926   69.688719   0.02300   60.365500   
Speed           24140.0     3.316080    3.518064  -0.28754    0.367580   
Shift           24140.0     0.727506    1.153951   0.00000    0.000000   
Load            24140.0     6.183771    4.502633  -1.00000    3.176000   
Acc _Total      24140.0     0.096554    1.006472  -3.19780   -0.409835   
RPM             24140.0  1266.539583  494.751789  -1.00000  879.287500   
Pitch           24140.0     0.558896    4.492549 -17.30100   -0.555400   
Acc _Lat        24140.0     0.029944    0.291206  -1.26720   -0.007239   
Passengers      24140.0     0.000000    0.000000   0.00000    0.000000   
Car_Load        24140.0     3.000000    0.000000   3.00000    3.000000   
AC_Con          24140.0     0.000000    0.000000   0.00000    0.000000   
Window_Open     24140.0     5.000000    0.000000   5.00000    5.000000   
Radio_volume    24140.0     0.000000    0.000000   0.00000    0.000000   
Rain_intensity  24140.0     0.000000    0.000000   0.00000    0.000000   
Visibility      24140.0    10.000000    0.000000  10.00000   10.000000   
welbeing        24140.0     2.000000    0.000000   2.00000    2.000000   
Rush            24140.0     0.000000    0.000000   0.00000    0.000000   
class           24140.0     0.497059    0.500002   0.00000    0.000000   

                        50%          75%        max  
Time             120.715000   181.062500   241.4200  
Speed              1.708150     5.963625    23.8020  
Shift              0.000000     1.000000     4.0000  
Load               3.740000     7.849650    24.0040  
Acc _Total         0.076712     0.646625     3.6817  
RPM             1074.550000  1576.225000  2944.7000  
Pitch              1.185600     2.916800    10.6980  
Acc _Lat           0.000007     0.044178     2.0127  
Passengers         0.000000     0.000000     0.0000  
Car_Load           3.000000     3.000000     3.0000  
AC_Con             0.000000     0.000000     0.0000  
Window_Open        5.000000     5.000000     5.0000  
Radio_volume       0.000000     0.000000     0.0000  
Rain_intensity     0.000000     0.000000     0.0000  
Visibility        10.000000    10.000000    10.0000  
welbeing           2.000000     2.000000     2.0000  
Rush               0.000000     0.000000     0.0000  
class              0.000000     1.000000     1.0000

In [8]:
data.shape

(24140, 18)

In [9]:
X = data.drop('class',axis=1)
y = data['class']

In [43]:
ccf_train_data = "./data/2018_4_21_22_38_train.csv"
ccf_test_data = "./data/2018_4_30_08_33_test.csv"


def load_data(filepath):
    from numpy import genfromtxt

    csv_data = genfromtxt(filepath, delimiter=",", skip_header=1)
    data = []
    labels = []

    for d in csv_data:
        data.append(d[:-1])
        labels.append(d[-1])

    return np.array(data), np.array(labels)

train_dataset, train_labels = load_data(ccf_train_data)
test_dataset, test_labels = load_data(ccf_test_data)

In [44]:
train_pl = tf.placeholder("float", [None, 17])
test_pl = tf.placeholder("float", [17])

knn_prediction = tf.reduce_sum(tf.abs(tf.add(train_pl, tf.negative(test_pl))), axis=1)

pred = tf.argmin(knn_prediction, 0)

with tf.Session() as tf_session:
    missed = 0

    for i in range(len(test_dataset)):
        knn_index = tf_session.run(pred, feed_dict={train_pl: train_dataset, test_pl: test_dataset[i]})
        
        print("Predicted class {} -- True class {}".format(train_labels[knn_index], test_labels[i]))
        
        if train_labels[knn_index] != test_labels[i]:
            missed += 1

    tf.summary.FileWriter("./samples/article/logs", tf_session.graph)
    

Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted cl

Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted cl

Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted cl

Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted cl

Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted class 1.0 -- True class 1.0
Predicted cl

...

Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted cl

Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted cl

Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted cl

Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted cl

Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted class 1.0 -- True class 0.0
Predicted cl

In [45]:
print("Missed: {} -- Total: {}".format(missed, len(test_dataset)))

Missed: 38628 -- Total: 100000


In [46]:
accuracy = (1-(missed/len(test_dataset)))
print("Accuracy : " , accuracy*100)

Accuracy :  61.37200000000001
